### Create a Spark session named "Table Loading" and obtain the Spark context


In [0]:
# Creating a Spark session
from pyspark.sql import SparkSession

spark_session = SparkSession.builder.appName("Table Loading").getOrCreate()
spark_context = spark_session.sparkContext


*Display the contents*

In [0]:
display(
    dbutils.fs.ls("/mnt/mydatalakefilesystem/Capstone2")
)

path name size modificationTime dbfs:/mnt/mydatalakefilesystem/Capstone2/DailyDeletedLog/ DailyDeletedLog/ 0 0 dbfs:/mnt/mydatalakefilesystem/Capstone2/ML_Training/ ML_Training/ 0 0 dbfs:/mnt/mydatalakefilesystem/Capstone2/incremetal_pl/ incremetal_pl/ 0 0 dbfs:/mnt/mydatalakefilesystem/Capstone2/postTypes/ postTypes/ 0 0 dbfs:/mnt/mydatalakefilesystem/Capstone2/posts/ posts/ 0 0 dbfs:/mnt/mydatalakefilesystem/Capstone2/users/ users/ 0 0

####Read Parquet files from Azure blob storage into 'posts_df' DataFrame and display it.


In [0]:
dbutils.fs.rm("/mnt/mydatalakefilesystem/Capstone2/ML_Training/Posts/", True)
dbutils.fs.rm("/mnt/mydatalakefilesystem/Capstone2/ML_Training/postTypes/", True)
dbutils.fs.rm("/mnt/mydatalakefilesystem/Capstone2/ML_Training/users/", True)

dbutils.fs.cp("/mnt/mydatalakefilesystem/Capstone2/posts/", "/mnt/mydatalakefilesystem/Capstone2/ML_Training/Posts/", True)

dbutils.fs.cp("/mnt/mydatalakefilesystem/Capstone2/postTypes/", "/mnt/mydatalakefilesystem/Capstone2/ML_Training/postTypes/", True)

dbutils.fs.cp("/mnt/mydatalakefilesystem/Capstone2/users/", "/mnt/mydatalakefilesystem/Capstone2/ML_Training/users/", True)

True

In [0]:
# Creating the posts dataframe
file_location = "/mnt/mydatalakefilesystem/Capstone2/ML_Training/Posts/*"

posts_df = spark.read \
  .parquet(file_location)

display(posts_df)

id AcceptedAnswerId AnswerCount Body CommentCount CreationDate FavoriteCount LastEditDate LastEditorDisplayName LastEditorUserId OwnerUserId ParentId PostTypeId Score Tags Title ViewCount 10531977 10532485 1 Ok, capturing key codes from special symbols produces different results on keyboards with different layouts. But how about the 'common' characters, like a-z? If you have a QWERTY-keyboard, you'd get key code 81 when you type q . When you have an AZERTY-keyboard, do you get code 81 when you press a , since a is where q 'should' be? Or is the mapping done differently? EDIT: The answer I accepted is probably the best solution when you're capturing keys and want to be sure 'a' is really 'a', but as I explain in the comment underneath that, I still am curious how the key codes are 'translated' when using int'l keyboards. That is: sources suggest at least a-z should be consistent, but I cannot find support for this (or someone who actually tried). 2 2024-05-10 1 2024-05-14 NULL 1005334 1005334 0 1 2.0 Key code for common characters on international keyboards 2169 10527274 0 0 To get the api to return JSON change the parameter client=t to client=p 3 2024-05-10 0 2024-05-14 NULL 215068 1386085 6599098 2 9.0 NULL NULL 0 10534618 0 0 Those tags are used by the Pervasive Integration tools. After having contacted Pervasive, I have confirmed these tags are not publicly documented. A potential user must contact Pervasive (http://www.pervasiveintegration.com). 0 2024-05-10 0 2024-05-14 NULL 314193 314193 10533159 2 0.0 NULL NULL 0 10510574 0 2 I have an application running Python 2.6.X. Starting the Python interpreter in interactive mode (with or without using virtualenv): readline support working (command history). Starting my application with the same Python interpreter (virtualenv-ed or not): no readline support available when using pdb.set_trace() : cursor keys not working. Operating system is Linux. 0 2024-05-09 0 2024-05-14 NULL 1897 2665694 0 1 12.0 No readline support while using pdb.set_trace() 872 10530232 10576535 2 I know there are a lot of questions targeting this issue. Although there are many good naming convention suggestions out there, we had a debate in our team. A team member insist that we should name our table's like that: sProducts and the primary key like that: ProductGuid There are two prefixe's in his system (s, h) so s stands for static and h - sorry i really don't know. I can see absolutely no logic in there. He says that every big oracle and ibm system is working like that. I've never worked with a oracle or ibm system, so is there a convention for adding prefixes like s and h? And what do they stand for? Somebody out there, who does the same? I'm sorry for that question - but I don't want to always add an s and have no clue why... 3 2024-05-10 1 2024-05-14 NULL 374988 374988 0 1 0.0 Database naming convention - prefix 903 10532654 10532733 2 I am developing a iPhone photo app in which there is one view, where I am showing all the images taken through that app with the help of uiscrollview. First I simply loaded the scrollview with all the present images. But it made the app slow and also caused the crash giving the following warning: Received memory warning. Level=2 I googled a lot and found that the reason for so may be loading such heavy images all together on a view are resulting in memory warning and crash afterwards. So I opt for the concept of lazy loading. In which I was just loading the three images one at the center(currently shown to user) and the other two on either sides. I did that in following way: - (void)scrollViewDidEndDecelerating:(UIScrollView *)scrollView { pageNum = (int)(scrollView.contentOffset.x / scrollView.frame.size.width); pageNumber = floor(pageNum); [self setImages:pageNumber]; //setting three images } Now there is no crash, no memory warning but the scroll has become quite rough with lots of jerks. Please suggest me how to get rid the roughness or to show all the images same as 

*Importing necessary libraries*

In [0]:
# Importing necessary libraries for defining schema
from pyspark.sql.types import StructType, StructField, IntegerType, StringType

# Defining the schema for the table storing post types
post_types_schema = StructType([
    # Defining the structure of the 'id' column
    StructField("id", IntegerType(), nullable=True),
    # Defining the structure of the 'Type' column
    StructField("Type", StringType(), nullable=True)
])


#### Set the file location for the post types data, read it into a DataFrame, apply the specified schema, and display the DataFrame.


In [0]:
# Setting the file location for the post types data
file_location = "/mnt/mydatalakefilesystem/Capstone2/ML_Training/postTypes/rds-postTypes.csv"

# Reading the post types data into a DataFrame
post_types_df = (spark.read
    # Specifying that the file has a header row
    .option("header", "true")
    # Specifying the separator used in the file
    .option("sep", ",")
    # Applying the schema defined earlier to enforce data types
    .schema(post_types_schema)
    # Loading the data from the specified file location
    .csv(file_location))

# Displaying the DataFrame containing post types
display(post_types_df)


id Type 1 Question 2 Answer 3 Wiki 4 TagWikiExerpt 5 TagWiki 6 ModeratorNomination 7 WikiPlaceholder 8 PrivilegeWiki

#### Define the schema for the users table with fields such as id, Age, CreationDate,etc...


In [0]:
# Creating the schema for the users table
from pyspark.sql.types import *

users_schema = StructType([
    StructField("id", IntegerType(), True),
    StructField("Age", IntegerType(), True),
    StructField("CreationDate", DateType(), True),
    StructField("DisplayName", StringType(), True),
    StructField("DownVotes", IntegerType(), True),
    StructField("EmailHash", StringType(), True),
    StructField("Location", StringType(), True),
    StructField("Reputation", IntegerType(), True),
    StructField("UpVotes", IntegerType(), True),
    StructField("Views", IntegerType(), True),
    StructField("WebsiteUrl", StringType(), True),
    StructField("AccountId", IntegerType(), True)
])

#### Set the file location for the users data, read it into a DataFrame, apply the specified schema, and display the DataFrame.


In [0]:
# Set the file location for the users data
file_location = "/mnt/mydatalakefilesystem/Capstone2/ML_Training/users/rds-Users.csv"

# Read the users data into a DataFrame
users_df = (spark.read
    .option("header", "true")
    .option("sep", ",")
    .schema(users_schema)
    .csv(file_location))

# Display the DataFrame containing users
display(users_df)


id Age CreationDate DisplayName DownVotes EmailHash Location Reputation UpVotes Views WebsiteUrl AccountId 340257 null 2018-05-13 Andri 0 NULL Copenhagen, Denmark 133 10 35 NULL 136631 340258 null 2018-05-13 Martin Hutchinson 0 NULL NULL 298 10 39 NULL 136632 340261 null 2018-05-13 Shanan 0 NULL NULL 1 0 4 NULL 612710 340265 null 2018-05-13 Heath Lilley 2 NULL NULL 298 80 73 NULL 136637 340266 null 2018-05-13 neebz 23 NULL Chicago, IL, United States 8987 467 537 null 136638 340269 null 2018-05-13 Dan 0 NULL NULL 6 0 0 NULL 612712 340270 null 2018-05-13 tiny_clanger 0 NULL NULL 1 0 0 NULL 612713 340271 null 2018-05-13 Wayne 0 NULL NULL 1 0 9 NULL 612714 340272 null 2018-05-13 Kipper 0 NULL NULL 81 0 3 http://www.codecraft.co.uk 612715 340273 null 2018-05-02 user340273 0 NULL NULL 21 0 6 NULL 136640 340276 null 2018-05-13 andragon 0 NULL NULL 518 6 13 null 136643 340277 null 2018-05-13 sam 19 NULL NULL 636 160 380 NULL 136644 340279 null 2018-05-13 Ofri Dagan 0 NULL NULL 21 0 6 NULL 612716 340281 null 2018-05-13 Anders Petersson 0 NULL Sweden 156 13 22 http://kiwiembedded.com 136647 340283 null 2018-05-13 droid-test 0 NULL NULL 16 0 6 NULL 612717 340284 null 2018-05-13 Dhruven Shah 0 NULL NULL 6 0 16 NULL 612718 340285 null 2018-05-13 Sanjeet Daga 0 NULL NULL 31 0 3 NULL 612719 340286 null 2018-05-13 Vicky 0 NULL Bangalore, India 562 92 92 null 136649 340287 null 2018-05-13 lukesky 0 NULL NULL 11 0 2 NULL 136650 340288 null 2018-05-13 Nitin 0 NULL NULL 1 0 2 NULL 612720 340290 null 2018-05-13 manikanta 2 NULL India 5545 972 524 https://manikanta.com 136651 340292 null 2018-05-13 moshe 0 NULL NULL 72 18 21 NULL 136653 340293 null 2018-05-13 edeevans 0 NULL Houston, TX 60 4 5 NULL 136654 340295 null 2018-05-13 blub 0 NULL NULL 1 0 3 http://rgwefr 612722 340296 null 2018-05-13 cmon_stoke 0 NULL Middleburg, VA 13 1 12 NULL 136656 340297 null 2018-05-13 Catalin Hritcu 0 NULL Paris 403 180 71 http://prosecco.gforge.inria.fr/personal/hritcu/ 136657 340298 null 2018-05-13 moliware 40 NULL Valencia, Spain 7566 406 332 http://moliware.com 136658 340299 null 2018-05-13 Alinboss 0 NULL NULL 1 0 3 NULL 612723 340300 null 2018-05-13 selfthinker 3 NULL London, United Kingdom 398 10 45 http://cv.selfthinker.org 136659 340302 null 2018-05-13 Peter 0 NULL NULL 171 0 2 NULL 612725 340306 null 2018-05-13 George 0 NULL NULL 11 0 4 NULL 612728 340307 null 2018-05-13 DrStrngeluv 0 NULL NULL 324 3 7 NULL 136661 340308 null 2018-05-13 ben 0 NULL NULL 1 0 3 NULL 612729 340309 null 2018-05-13 user340309 0 NULL NULL 21 1 1 NULL 136662 340310 null 2018-05-13 Andy 0 NULL NULL 28 0 2 NULL 612730 340312 null 2018-05-13 PBK 0 NULL NULL 41 0 0 NULL 612731 340313 null 2018-05-13 marco sangiorgi 0 NULL NULL 1 0 1 NULL 612732 340315 null 2018-05-13 Rohit 0 NULL NULL 1 0 3 NULL 612734 340317 null 2018-05-13 Josh 0 NULL NULL 11 0 0 NULL 612735 340318 null 2018-05-13 torn 0 NULL NULL 539 2 30 NULL 136665 340319 null 2018-05-13 Serenity 0 NULL NULL 56 0 12 NULL 612736 340322 null 2018-05-13 Fabiano Francesconi 9 NULL Zurich, Switzerland 1421 67 206 http://blog.encomiabile.it 136667 340323 null 2018-05-13 Parker 0 NULL Washington, DC 1 0 19 NULL 136668 340324 null 2018-05-13 Ian 0 NULL NULL 27 4 3 NULL 136669 340325 null 2018-05-13 ClearCarbon 0 NULL Sheffield, United Kingdom 15 2 6 http://www.clear-carbon.co.uk 136670 340326 null 2018-05-13 Alexandru 0 NULL Romania 11 0 7 http://alex.bumbacea.ro 136671 340328 null 2018-05-13 Oleg Anastasyev 0 NULL NULL 1 0 8 NULL 612737 340329 null 2018-05-13 Kris 0 NULL NULL 11 0 4 NULL 612738 340330 null 2018-05-13 gaurav awasthi 0 NULL NULL 1 0 2 NULL 612739 340331 null 2018-05-13 etarvt 0 NULL NULL 23 0 5 NULL 136673 340332 null 2018-05-13 David 0 NULL NULL 11 0 4 NULL 612740 340334 null 2018-05-13 JohnGB 4 NULL Delft, Netherlands 642 251 127 null 136675 340335 null 2018-05-13 Pieter van Niekerk 5 NULL South Africa 623 926 245 http://twitter.com/pietervniekerk 136676 340337 null 2018-05-13 Chuck 0 NULL NULL 1 0 0 NULL 612742 340338

#### Save the DataFrames 'posts_df', 'post_types_df', and 'users_df' to the Databricks local file system 


In [0]:
# Save the 3 tables to Databricks local file system 
posts_df.write.mode("overwrite").parquet("/tmp/project/posts")
post_types_df.write.mode("overwrite").parquet("/tmp/project/PostTypes")
users_df.write.mode("overwrite").parquet("/tmp/project/user")

*Display the contents*

In [0]:
# review the local file system
display(dbutils.fs.ls("/tmp/project/"))

path name size modificationTime dbfs:/tmp/project/PostTypes/ PostTypes/ 0 1716668835000 dbfs:/tmp/project/posts/ posts/ 0 1716668664000 dbfs:/tmp/project/preprocessed_data/ preprocessed_data/ 0 1716674401000 dbfs:/tmp/project/user/ user/ 0 1716668920000